In [14]:
import pandas as pd
from sklearn.model_selection import train_test_split
from statsmodels.stats.outliers_influence import variance_inflation_factor
import sklearn
import statsmodels
import statsmodels.formula.api as sm
import matplotlib.pyplot as plt
import seaborn as sns
import copy
import requests
import pprint
from urllib import parse
from bs4 import BeautifulSoup

# 지수 형태의 실수를 소수점 3자리까지 표기
pd.options.display.float_format = "{:.3f}".format

# 공유 폴더 경로
dirShare = "G:/.shortcut-targets-by-id/188U2ypi3eUvuInaixMTTbbFctprRo9e4/GYM살라빔"


In [25]:
# 라이브러리 버전 확인
print("pandas 현재 버전 : " + pd.__version__)
print("scikit-learn 현재 버전 : " + sklearn.__version__)
print("statsmodels 현재 버전 : " + statsmodels.__version__)

pandas 현재 버전 : 2.0.3
scikit-learn 현재 버전 : 1.3.0
statsmodels 현재 버전 : 0.14.0


# 데이터 불러오고 전처리

In [15]:
# train.csv 데이터 프레임으로 불러오기
df = pd.read_csv(dirShare+"/data/train.csv")

# df 정보 확인
df.info()

# df 상위 10개 불러오기
df.head(10)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 301 entries, 0 to 300
Data columns (total 58 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   inst_id             301 non-null    int64  
 1   OC                  301 non-null    object 
 2   sido                301 non-null    object 
 3   sgg                 301 non-null    int64  
 4   openDate            301 non-null    int64  
 5   bedCount            296 non-null    float64
 6   instkind            300 non-null    object 
 7   revenue1            293 non-null    float64
 8   salescost1          293 non-null    float64
 9   sga1                293 non-null    float64
 10  salary1             293 non-null    float64
 11  noi1                293 non-null    float64
 12  noe1                293 non-null    float64
 13  interest1           293 non-null    float64
 14  ctax1               293 non-null    float64
 15  profit1             293 non-null    float64
 16  liquidAs

inst_id    OC       sido  sgg  openDate  bedCount          instkind  \
0        1  open  choongnam   73  20071228   175.000  nursing_hospital   
1        3  open  gyeongnam   32  19970401   410.000  general_hospital   
2        4  open   gyeonggi   89  20161228   468.000  nursing_hospital   
3        7  open    incheon  141  20000814   353.000  general_hospital   
4        9  open  gyeongnam   32  20050901   196.000  general_hospital   
5       11  open  gyeongnam  155  20020501   243.000  general_hospital   
6       14  open   gyeonggi  169  19820702   213.000  general_hospital   
7       15  open      busan   66  19871102   250.000  general_hospital   
8       16  open    jeonnam   91  20060922   280.000  nursing_hospital   
9       17  open      seoul    4  20000124    55.000  general_hospital   

         revenue1      salescost1            sga1  ...           debt2  \
0  4217530010.000           0.000  3961134739.000  ...   758993742.000   
1             NaN             NaN             NaN  ...             NaN   
2  1004521989.000   515483669.000   447219722.000  ...           0.000   
3 72507342181.000           0.000 70677397660.000  ... 37755010512.000   
4 49043538016.000           0.000 47656051197.000  ... 51432592890.000   
5 33580536703.000  9222996930.000 23727912054.000  ...           0.000   
6 22552179836.000  4449958166.000 16573328452.000  ... 19642026834.000   
7 64359169160.000 20758010719.000 40882537264.000  ... 35984818131.000   
8 12748392940.000   328697683.000 11076189315.000  ...           0.000   
9 41406077905.000  6624671265.000 35120182720.000  ... 34906729636.000   

   liquidLiabilities2      shortLoan2  NCLiabilities2       longLoan2  \
0       222876855.000           0.000   536116887.000   390000000.000   
1                 NaN             NaN             NaN             NaN   
2               0.000           0.000           0.000           0.000   
3     17018596586.000  9219427379.000 20736413926.000 15100000000.000   
4     30072585842.000 17593752360.000 21360007048.000 14108027465.000   
5     21861133888.000 17087136895.000    20000000.000           0.000   
6     13292026834.000 12155602473.000  6350000000.000  6230000000.000   
7     11219645317.000           0.000 24765172814.000 16000000000.000   
8     13113246330.000 12664417803.000    41962676.000           0.000   
9     19675893406.000 16365396427.000 15230836230.000  3400000000.000   

        netAsset2       surplus2  employee1  employee2  ownerChange  
0  2619290493.000 1271224493.000     62.000     64.000         same  
1             NaN            NaN    801.000    813.000         same  
2           0.000          0.000    234.000      1.000         same  
3 12954271998.000 7740829037.000    663.000    663.000         same  
4     5561941.000 9025549604.000    206.000    197.000         same  
5           0.000 5879003604.000    397.000    390.000         same  
6 18888294786.000 9174282922.000    221.000    246.000         same  
7 14217864484.000 9177282701.000    489.000    489.000         same  
8           0.000          0.000    243.000    243.000         same  
9 20244525873.000 9554580715.000    370.000    382.000         same  

[10 rows x 58 columns]

In [27]:
# 데이터 개수 확인하기
print("데이터 개수 : ", df.shape[0])

데이터 개수 :  301


In [28]:
# 숫자 형식의 컬럼의 기술통계값을 출력
df.describe()

inst_id     sgg     openDate  bedCount         revenue1  \
count  301.000 301.000      301.000   296.000          293.000   
mean   219.056  81.040 20050125.801   145.709  12881747447.993   
std    121.235  50.970    88938.154   118.924  20435433475.616   
min      1.000   1.000 19780124.000     0.000            0.000   
25%    112.000  37.000 20011017.000    52.750   3252111902.000   
50%    230.000  75.000 20071126.000   136.500   5524218104.000   
75%    321.000 123.000 20111021.000   193.000  12748392940.000   
max    428.000 178.000 20170607.000   656.000 151000000000.000   

           salescost1             sga1         salary1           noi1  \
count         293.000          293.000         293.000        293.000   
mean   2014902794.594  10332439064.089  5654114566.904  269615124.573   
std    7460270656.568  14938862491.946  8083342530.256  802370115.514   
min             0.000            0.000           0.000          0.000   
25%             0.000   2758200772.000  1626052720.000    8217133.000   
50%     210410492.000   4684074465.000  2659892367.000   43637641.000   
75%     910527771.000  10778762060.000  6363400069.000  205033071.000   
max   98503322990.000 103000000000.000 64035593950.000 9144170639.000   

                noe1  ...  receivableL2           debt2  liquidLiabilities2  \
count        293.000  ...       293.000         293.000             293.000   
mean   511587022.570  ...    222670.000  8146026488.788      3860583593.406   
std   1060379255.452  ...   3811496.447 12557995349.365      6797242094.076   
min            0.000  ...         0.000           0.000               0.000   
25%     80133952.000  ...         0.000  1283220350.000       285574118.000   
50%    183196506.000  ...         0.000  3784552900.000      1454049945.000   
75%    420333030.000  ...         0.000  8465053127.000      4364713622.000   
max   8686379500.000  ...  65242310.000 85088583901.000     68468775764.000   

           shortLoan2  NCLiabilities2       longLoan2        netAsset2  \
count         293.000         293.000         293.000          293.000   
mean   1510050431.986  4471247363.877  2709978815.423   5273919018.089   
std    2953412250.368  7659580436.397  4564001070.999  10812593821.248   
min             0.000           0.000           0.000 -20147802018.000   
25%             0.000    25578782.000           0.000   1017572570.000   
50%      85425488.000  1969746813.000  1100000000.000   2894969804.000   
75%    1567966980.000  4905441439.000  3360000000.000   5370284792.000   
max   17593752360.000 51503883627.000 32561472110.000 125000000000.000   

             surplus2  employee1  employee2  
count         293.000    291.000    288.000  
mean    978627865.256    142.546    134.326  
std    4688797890.975    160.191    151.062  
min   -2781506722.000      0.000      0.000  
25%             0.000     53.500     53.750  
50%             0.000     80.000     79.000  
75%     101444685.000    181.500    170.000  
max   68527297093.000   1200.000   1200.000  

[8 rows x 54 columns]

In [29]:
# 컬럼별 null 값 확인하기
df.shape[0] - df.count()

inst_id                0
OC                     0
sido                   0
sgg                    0
openDate               0
bedCount               5
instkind               1
revenue1               8
salescost1             8
sga1                   8
salary1                8
noi1                   8
noe1                   8
interest1              8
ctax1                  8
profit1                8
liquidAsset1           8
quickAsset1            8
receivableS1           8
inventoryAsset1        8
nonCAsset1             8
tanAsset1              8
OnonCAsset1            8
receivableL1           8
debt1                  8
liquidLiabilities1     8
shortLoan1             8
NCLiabilities1         8
longLoan1              8
netAsset1              8
surplus1               8
revenue2               8
salescost2             8
sga2                   8
salary2                8
noi2                   8
noe2                   8
interest2              8
ctax2                  8
profit2                8


In [30]:
# 아직 운영 중인 병원을 1로 변환
df.replace({"open":1},inplace=True)
# 폐업한 병원을 0으로 변환
df.replace({" close":0}, inplace=True)
# unique() 메서드를 통해 "OC" 컬럼의 데이터를 확인
df["OC"].unique()

array([1, 0], dtype=int64)

In [31]:
# 병원 정보에 NULL이 존재하는 부분을 다른 값으로 대체할 수 없음
# 병원의 매출, 비용, 이익, 직원 수와 같은 값을 다른 병원의 평균이나 중앙값으로 대체하면 안 됨
df.dropna(axis=0, inplace=True)

In [32]:
# df_loca = df[["sido","sgg"]]
# df_loca.sort_values(by=["sido"], axis=0, ascending=True)

In [33]:
# 데이터 값이 0으로만 돼 있는 컬럼 삭제
df.drop(columns=["receivableL1", "receivableL2"], axis=1, inplace=True)
# 시군구 코드 삭제
df.drop(columns="sgg", axis=1, inplace=True)
# 병원 id는 분석에 있어서 의미가 없는 데이터이므로 삭제
df.drop(columns="inst_id",inplace=True)
# 데이터 프레임에서 drop 됐는지 확인
df.columns

Index(['OC', 'sido', 'openDate', 'bedCount', 'instkind', 'revenue1',
       'salescost1', 'sga1', 'salary1', 'noi1', 'noe1', 'interest1', 'ctax1',
       'profit1', 'liquidAsset1', 'quickAsset1', 'receivableS1',
       'inventoryAsset1', 'nonCAsset1', 'tanAsset1', 'OnonCAsset1', 'debt1',
       'liquidLiabilities1', 'shortLoan1', 'NCLiabilities1', 'longLoan1',
       'netAsset1', 'surplus1', 'revenue2', 'salescost2', 'sga2', 'salary2',
       'noi2', 'noe2', 'interest2', 'ctax2', 'profit2', 'liquidAsset2',
       'quickAsset2', 'receivableS2', 'inventoryAsset2', 'nonCAsset2',
       'tanAsset2', 'OnonCAsset2', 'debt2', 'liquidLiabilities2', 'shortLoan2',
       'NCLiabilities2', 'longLoan2', 'netAsset2', 'surplus2', 'employee1',
       'employee2', 'ownerChange'],
      dtype='object')

In [34]:
df_drop_obj = copy.deepcopy(df)
df_dr_obj_cols = df_drop_obj.columns.to_list()
# df_dr_obj_cols

In [35]:
df_drop_obj2 = copy.deepcopy(df_drop_obj)

# 컬럼 데이터 타입이 'object'인 컬럼 삭제
for i in range(len(df_dr_obj_cols)) : 
    if df_drop_obj.iloc[:,i].dtype == "object" : 
        df_drop_obj2.drop(columns=df_dr_obj_cols[i], inplace=True)

df_drop_obj = df_drop_obj2
df_drop_obj.info()

<class 'pandas.core.frame.DataFrame'>
Index: 277 entries, 0 to 296
Data columns (total 51 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   OC                  277 non-null    int64  
 1   openDate            277 non-null    int64  
 2   bedCount            277 non-null    float64
 3   revenue1            277 non-null    float64
 4   salescost1          277 non-null    float64
 5   sga1                277 non-null    float64
 6   salary1             277 non-null    float64
 7   noi1                277 non-null    float64
 8   noe1                277 non-null    float64
 9   interest1           277 non-null    float64
 10  ctax1               277 non-null    float64
 11  profit1             277 non-null    float64
 12  liquidAsset1        277 non-null    float64
 13  quickAsset1         277 non-null    float64
 14  receivableS1        277 non-null    float64
 15  inventoryAsset1     277 non-null    float64
 16  nonCAsset1   

In [36]:
# 병원 개/폐업 정보의 다중 회귀 분석과 검정 통계량 확인
Models1 = sm.ols("OC ~ " + "+".join(df_drop_obj.columns[1:]), data=df_drop_obj)
result1 = Models1.fit()
print(result1.summary())

                            OLS Regression Results                            
Dep. Variable:                     OC   R-squared:                       0.277
Model:                            OLS   Adj. R-squared:                  0.117
Method:                 Least Squares   F-statistic:                     1.731
Date:                Mon, 10 Jul 2023   Prob (F-statistic):            0.00383
Time:                        22:32:13   Log-Likelihood:                 164.83
No. Observations:                 277   AIC:                            -227.7
Df Residuals:                     226   BIC:                            -42.84
Df Model:                          50                                         
Covariance Type:            nonrobust                                         
                         coef    std err          t      P>|t|      [0.025      0.975]
--------------------------------------------------------------------------------------
Intercept              4.2750      2

In [37]:
# 독립변수 X와 종속변수 y로 분리
X = df_drop_obj.iloc[:,1:]
y = df_drop_obj.iloc[:,0]

In [39]:
# 독립변수들간 다중 공선성 확인, vif 지수 10 이상이면 변수 제거 고려
vif = pd.DataFrame()
vif["VIF Factor"] = [variance_inflation_factor(X.values,i) for i in range(X.shape[1])]
vif["features"] = X.columns
vif = vif.sort_values("VIF Factor").reset_index(drop=True)
vif

VIF Factor            features
0        2.366            bedCount
1        3.737            openDate
2        6.340        receivableS2
3        6.494        receivableS1
4       12.035          shortLoan2
5       14.965          shortLoan1
6       20.043         OnonCAsset2
7       20.224         OnonCAsset1
8       22.919           interest1
9       24.217           interest2
10      29.897            surplus2
11      31.027           employee2
12      41.860           employee1
13      48.952           longLoan2
14      49.235     inventoryAsset2
15      54.158           longLoan1
16      73.027            surplus1
17      90.878     inventoryAsset1
18     444.396               ctax1
19     458.244               ctax2
20     875.933             salary2
21     890.690             salary1
22    1660.333           tanAsset1
23    2097.574           tanAsset2
24    2439.246                noi2
25    4291.453                noi1
26    5106.947         quickAsset2
27    7295.320                noe1
28    8160.759             profit1
29   10810.648             profit2
30   11148.307                noe2
31   24079.756         quickAsset1
32  119411.267        liquidAsset1
33  251612.232        liquidAsset2
34  371660.042          salescost1
35  408022.937           netAsset1
36  408155.510          salescost2
37  459567.970  liquidLiabilities1
38  554973.927               debt2
39  611602.006               debt1
40  679487.737      NCLiabilities1
41  736307.160          nonCAsset1
42  849957.884           netAsset2
43  910385.951  liquidLiabilities2
44 1168339.480      NCLiabilities2
45 1471435.214                sga1
46 1622510.398                sga2
47 1972381.814          nonCAsset2
48 2720979.309            revenue1
49 3183231.571            revenue2

In [44]:
# vif 지수가 10미만인 컬럼명
vif[vif["VIF Factor"]<10.0]["features"]

0        bedCount
1        openDate
2    receivableS2
3    receivableS1
Name: features, dtype: object

In [46]:
df_drop_vif = df_drop_obj[["OC","bedCount", "openDate", "receivableS2", "receivableS1"]]

In [47]:
Models2 = sm.ols("OC ~ " + "+".join(df_drop_vif.columns[1:]), data=df_drop_vif)
result2 = Models2.fit()
print(result2.summary())

                            OLS Regression Results                            
Dep. Variable:                     OC   R-squared:                       0.021
Model:                            OLS   Adj. R-squared:                  0.006
Method:                 Least Squares   F-statistic:                     1.436
Date:                Mon, 10 Jul 2023   Prob (F-statistic):              0.222
Time:                        22:50:24   Log-Likelihood:                 122.81
No. Observations:                 277   AIC:                            -235.6
Df Residuals:                     272   BIC:                            -217.5
Df Model:                           4                                         
Covariance Type:            nonrobust                                         
                   coef    std err          t      P>|t|      [0.025      0.975]
--------------------------------------------------------------------------------
Intercept        3.6487      2.205      1.655   

In [ ]:
"""
vif 지수가 10 이상이라고 무조건 제거하면 안 됨!
"""

# 병원 정보 api 불러오기

In [ ]:
"""
https://apis.data.go.kr/B551182/hospInfoServicev2/getHospBasisList?serviceKey=repbMvjCXw96iTs6wjKM3Htm1H480VcdawruKmikMmOYZF8aVD%2FrJDkfGoyLeTuS5Y1KEOzUrwwPIu87UQ9LbQ%3D%3D&pageNo=1&numOfRows=10&sidoCd=110000&sgguCd=110019&emdongNm=%EC%8B%A0%EB%82%B4%EB%8F%99&yadmNm=%EC%84%9C%EC%9A%B8%EC%9D%98%EB%A3%8C%EC%9B%90&zipCd=2010&clCd=11&dgsbjtCd=01&xPos=127.09854004628151&yPos=37.6132113197367&radius=3000
"""

In [3]:
serviceKey = "repbMvjCXw96iTs6wjKM3Htm1H480VcdawruKmikMmOYZF8aVD/rJDkfGoyLeTuS5Y1KEOzUrwwPIu87UQ9LbQ=="
serviceKeyDecoded = parse.unquote(serviceKey, 'UTF-8')

url = "http://apis.data.go.kr/B551182/hospInfoServicev2/getHospBasisList"
returnType="xml"
Pindex = 1
Psize = 1000


queryParams = '?' + parse.urlencode({ parse.quote_plus("serviceKey") : serviceKeyDecoded,
                                parse.quote_plus("numOfRows") : '10000',
                                parse.quote_plus("pageNo") : '1'
                                    })

res = requests.get(url + queryParams)

In [4]:
soup = BeautifulSoup(res.text, 'lxml-xml')
items = soup.find_all("item")

In [5]:
pprint.pprint(items)

[<item><addr>인천광역시 부평구 동수로 56, (부평동)</addr><clCd>01</clCd><clCdNm>상급종합</clCdNm><cmdcGdrCnt>0</cmdcGdrCnt><cmdcIntnCnt>0</cmdcIntnCnt><cmdcResdntCnt>0</cmdcResdntCnt><cmdcSdrCnt>0</cmdcSdrCnt><detyGdrCnt>1</detyGdrCnt><detyIntnCnt>0</detyIntnCnt><detyResdntCnt>0</detyResdntCnt><detySdrCnt>2</detySdrCnt><drTotCnt>340</drTotCnt><emdongNm>부평동</emdongNm><estbDd>19810806</estbDd><mdeptGdrCnt>1</mdeptGdrCnt><mdeptIntnCnt>24</mdeptIntnCnt><mdeptResdntCnt>69</mdeptResdntCnt><mdeptSdrCnt>243</mdeptSdrCnt><pnursCnt>0</pnursCnt><postNo>21431</postNo><sgguCd>220003</sgguCd><sgguCdNm>인천부평구</sgguCdNm><sidoCd>220000</sidoCd><sidoCdNm>인천</sidoCdNm><telno>032-1544-9004</telno><XPos>126.7248987</XPos><YPos>37.4848309</YPos><yadmNm>가톨릭대학교인천성모병원</yadmNm><ykiho>JDQ4MTYyMiM1MSMkMSMkMCMkODkkMzgxMzUxIzExIyQxIyQzIyQ3OSQyNjE4MzIjNDEjJDEjJDgjJDgz</ykiho></item>,
 <item><addr>강원특별자치도 강릉시 사천면 방동길 38, ()</addr><clCd>01</clCd><clCdNm>상급종합</clCdNm><cmdcGdrCnt>0</cmdcGdrCnt><cmdcIntnCnt>0</cmdcIntnCnt><cmdcResdntCnt>0<

In [6]:
def parse():
    try:
        ADDR = item.find("addr").get_text()
        CLCD = item.find("clCd").get_text()
        CLCDNM = item.find("clCdNm").get_text()
        EMDONGNM = item.find("emdongNm").get_text()
        ESTBDB = item.find("estbDd").get_text()
        POSTNO = item.find("postNo").get_text()
        SGGUCD = item.find("sgguCd").get_text()
        SGGUCDNM = item.find("sgguCdNm").get_text()
        SIDOCD = item.find("sidoCd").get_text()
        SIDOCDNM = item.find("sidoCdNm").get_text()
        XPOS = item.find("XPos").get_text()
        YPOS = item.find("YPos").get_text()
        YADMNM = item.find("yadmNm").get_text()
        YKIHO = item.find("ykiho").get_text()
        return {
            "주소":ADDR,
            "종별코드":CLCD,
            "종별코드명":CLCDNM,
            "읍면동":EMDONGNM,
            "개설일자":ESTBDB,
            "Post No.":POSTNO,
            "시군구코드":SGGUCD,
            "시군구코드명":SGGUCDNM,
            "시도코드":SIDOCD,
            "시도코드명":SIDOCDNM,
            "x좌표":XPOS,
            'y좌표':YPOS,
            "요양기관명":YADMNM,
            "암호화요양기호":YKIHO
        }
    except AttributeError as e:
        return {
            "주소":None,
            "종별코드":None,
            "종별코드명":None,
            "읍면동":None,
            "개설일자":None,
            "Post No.":None,
            "시군구코드":None,
            "시군구코드명":None,
            "시도코드":None,
            "시도코드명":None,
            "x좌표":None,
            'y좌표':None,
            "요양기관명":None,
            "암호화요양기호":None
        }

In [7]:
row = list()

for item in items : 
    row.append(parse())

In [8]:
df_api = pd.DataFrame(row)
df_api.head()

주소  종별코드 종별코드명   읍면동      개설일자 Post No.   시군구코드  \
0  인천광역시 부평구 동수로 56, (부평동)    01  상급종합   부평동  19810806    21431  220003   
1                     None  None  None  None      None     None    None   
2                     None  None  None  None      None     None    None   
3                     None  None  None  None      None     None    None   
4                     None  None  None  None      None     None    None   

  시군구코드명    시도코드 시도코드명          x좌표         y좌표         요양기관명  \
0  인천부평구  220000    인천  126.7248987  37.4848309  가톨릭대학교인천성모병원   
1   None    None  None         None        None          None   
2   None    None  None         None        None          None   
3   None    None  None         None        None          None   
4   None    None  None         None        None          None   

                                             암호화요양기호  
0  JDQ4MTYyMiM1MSMkMSMkMCMkODkkMzgxMzUxIzExIyQxIy...  
1                                               None  
2                                               None  
3                                               None  
4                                               None

In [13]:
df_api.dropna(axis=0, how="any", inplace=True)
df_api.shape

(2609, 14)

In [18]:
df_api.to_csv(dirShare+"/data/병원정보api.csv",sep=',', encoding="utf-8")